In [27]:
import numpy as np
import pandas as pd
from math import sqrt

In [28]:
critics={'Lisa Rose': {'Lady in the Water': 2.5, 'Snakes on a Plane': 3.5,
 'Just My Luck': 3.0, 'Superman Returns': 3.5, 'You, Me and Dupree': 2.5, 
 'The Night Listener': 3.0},
'Gene Seymour': {'Lady in the Water': 3.0, 'Snakes on a Plane': 3.5, 
 'Just My Luck': 1.5, 'Superman Returns': 5.0, 'The Night Listener': 3.0, 
 'You, Me and Dupree': 3.5}, 
'Michael Phillips': {'Lady in the Water': 2.5, 'Snakes on a Plane': 3.0,
 'Superman Returns': 3.5, 'The Night Listener': 4.0},
'Claudia Puig': {'Snakes on a Plane': 3.5, 'Just My Luck': 3.0,
 'The Night Listener': 4.5, 'Superman Returns': 4.0, 
 'You, Me and Dupree': 2.5},
'Mick LaSalle': {'Lady in the Water': 3.0, 'Snakes on a Plane': 4.0, 
 'Just My Luck': 2.0, 'Superman Returns': 3.0, 'The Night Listener': 3.0,
 'You, Me and Dupree': 2.0}, 
'Jack Matthews': {'Lady in the Water': 3.0, 'Snakes on a Plane': 4.0,
 'The Night Listener': 3.0, 'Superman Returns': 5.0, 'You, Me and Dupree': 3.5},
'Toby': {'Snakes on a Plane':4.5,'You, Me and Dupree':1.0,'Superman Returns':4.0}}

In [29]:
df=pd.DataFrame(critics)
df

Lisa Rose  Gene Seymour  Michael Phillips  Claudia Puig  \
Just My Luck              3.0           1.5               NaN           3.0   
Lady in the Water         2.5           3.0               2.5           NaN   
Snakes on a Plane         3.5           3.5               3.0           3.5   
Superman Returns          3.5           5.0               3.5           4.0   
The Night Listener        3.0           3.0               4.0           4.5   
You, Me and Dupree        2.5           3.5               NaN           2.5   

                    Mick LaSalle  Jack Matthews  Toby  
Just My Luck                 2.0            NaN   NaN  
Lady in the Water            3.0            3.0   NaN  
Snakes on a Plane            4.0            4.0   4.5  
Superman Returns             3.0            5.0   4.0  
The Night Listener           3.0            3.0   NaN  
You, Me and Dupree           2.0            3.5   1.0

In [41]:
# 计算Pearson相关系数的函数
def computeSim_Pearson(datadict,p1,p2):
#     得到两边都有的信息记录
    sim={}
    for item in datadict[p1]:
        if item in datadict[p2]:
            sim[item] = 1
#     计算是否存在相同的记录
    n=len(sim)
    if n==0:
        return 1
    
#     计算所有偏好的和
    sum1=sum([datadict[p1][it] for it in sim])
    sum2=sum([datadict[p2][it] for it in sim])
    
#     计算平方和
    sum1Sq1=sum([pow(datadict[p1][it],2) for it in sim])
    sum1Sq2=sum([pow(datadict[p2][it],2) for it in sim])
                 
#     计算乘积和
    multiSum=sum([datadict[p1][it]*datadict[p2][it] for it in sim])
  
#     计算相关系数
    Num=multiSum-(sum1*sum2/n)
    den=sqrt((sum1Sq1-pow(sum1,2)/n)*(sum1Sq2-pow(sum2,2)/n))
    if den==0:
        return 0
    r=Num/den
    
    return r
computeSim_Pearson(critics,'Lisa Rose','Gene Seymour')  

0.39605901719066977

In [31]:
# 计算每一个User对其他User的相关系数,并排序
def computTopSim(datadict,item,n=5,similarity=computeSim_Pearson):
#     计算每个用户对其他用户的相关系数(不包括自己)
    scores=[(computeSim_Pearson(datadict,item,other),other) for other in datadict if other!=item]
    
#     对列表进行排序
    scores.sort()
    scores.reverse()
    return scores[0:n]

computTopSim(critics,'Toby',3)

{'Snakes on a Plane': 1, 'You, Me and Dupree': 1, 'Superman Returns': 1}
{'Snakes on a Plane': 1, 'You, Me and Dupree': 1, 'Superman Returns': 1}
{'Snakes on a Plane': 1, 'Superman Returns': 1}
{'Snakes on a Plane': 1, 'You, Me and Dupree': 1, 'Superman Returns': 1}
{'Snakes on a Plane': 1, 'You, Me and Dupree': 1, 'Superman Returns': 1}
{'Snakes on a Plane': 1, 'You, Me and Dupree': 1, 'Superman Returns': 1}


[(0.9912407071619299, 'Lisa Rose'),
 (0.9244734516419049, 'Mick LaSalle'),
 (0.8934051474415647, 'Claudia Puig')]

In [43]:
# 加权评价值进行推荐
def getRecommendations(dictset,person,similarity=computeSim_Pearson):
    totals={}
    simSums={}
    
    for other in dictset:
        #         如果是自己则跳过
        if other==person:
            continue
        sim=similarity(dictset,person,other)
#         忽略评价值小于等于0的情况
        if sim<=0:
            continue
        for item in dictset[other]:
#             对没有评分过的商品不做评价
            if item not in dictset[person] or dictset[person][item]==0:
#               相似度乘与评价分数
                totals.setdefault(item,0)
                totals[item]+=sim*dictset[other][item]
#               相似度总计
                simSums.setdefault(item,0)
                simSums[item]+=sim
    
    ranks=[(total/simSums[item],item) for item,total in totals.items()]               
    ranks.sort()
    ranks.reverse()
    return ranks
getRecommendations(critics,'Toby')

[(3.3477895267131017, 'The Night Listener'),
 (2.8325499182641614, 'Lady in the Water'),
 (2.530980703765565, 'Just My Luck')]

In [33]:
def transformDic(datadict):
    result={}
    for person in datadict:
        for item in datadict[person]:
            result.setdefault(item,{})
            result[item][person]=datadict[person][item]
    return result

newdict=transformDic(critics)
newdict

{'Lady in the Water': {'Lisa Rose': 2.5,
  'Gene Seymour': 3.0,
  'Michael Phillips': 2.5,
  'Mick LaSalle': 3.0,
  'Jack Matthews': 3.0},
 'Snakes on a Plane': {'Lisa Rose': 3.5,
  'Gene Seymour': 3.5,
  'Michael Phillips': 3.0,
  'Claudia Puig': 3.5,
  'Mick LaSalle': 4.0,
  'Jack Matthews': 4.0,
  'Toby': 4.5},
 'Just My Luck': {'Lisa Rose': 3.0,
  'Gene Seymour': 1.5,
  'Claudia Puig': 3.0,
  'Mick LaSalle': 2.0},
 'Superman Returns': {'Lisa Rose': 3.5,
  'Gene Seymour': 5.0,
  'Michael Phillips': 3.5,
  'Claudia Puig': 4.0,
  'Mick LaSalle': 3.0,
  'Jack Matthews': 5.0,
  'Toby': 4.0},
 'You, Me and Dupree': {'Lisa Rose': 2.5,
  'Gene Seymour': 3.5,
  'Claudia Puig': 2.5,
  'Mick LaSalle': 2.0,
  'Jack Matthews': 3.5,
  'Toby': 1.0},
 'The Night Listener': {'Lisa Rose': 3.0,
  'Gene Seymour': 3.0,
  'Michael Phillips': 4.0,
  'Claudia Puig': 4.5,
  'Mick LaSalle': 3.0,
  'Jack Matthews': 3.0}}

In [34]:
computTopSim(newdict,'The Night Listener')

{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}


[(0.5555555555555556, 'Just My Luck'),
 (-0.1798471947990544, 'Superman Returns'),
 (-0.250000000000002, 'You, Me and Dupree'),
 (-0.5663521139548527, 'Snakes on a Plane'),
 (-0.6123724356957927, 'Lady in the Water')]

In [35]:
getRecommendations(newdict,'Just My Luck')

{'Lisa Rose': 1, 'Gene Seymour': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
[(4.0, 'Michael Phillips'), (3.0, 'Jack Matthews')]


[(4.0, 'Michael Phillips'), (3.0, 'Jack Matthews')]

In [47]:
# 基于物品的推荐，在没个数据库更新之后执行一次，得到的数据可以拿来做推荐
# 得到一个字典。记录了每个物品的相关物品
def calculateSimItem(datadic,n=10):
    result={}
#     转换矩阵，以物品为中心
    itemDic=transformDic(datadic)
    
    c=0
    for item in itemDic:
        scores=computTopSim(itemDic,item,n=n)
        result[item]=scores
    return result

In [37]:
itemSim=calculateSimItem(critics)
itemSim

{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1, 'Toby': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1, 'Toby': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Michael Phillips': 1, 'Claudia Puig': 1, 'Mick LaSalle': 1, 'Jack Matthews': 1}
{'Lisa Rose': 1, 'Gene Seymour': 1, 'Mick LaSalle': 1}

{'Lady in the Water': [(0.7637626158259785, 'Snakes on a Plane'),
  (0.4879500364742689, 'Superman Returns'),
  (0.3333333333333333, 'You, Me and Dupree'),
  (-0.6123724356957927, 'The Night Listener'),
  (-0.9449111825230676, 'Just My Luck')],
 'Snakes on a Plane': [(0.7637626158259785, 'Lady in the Water'),
  (0.11180339887498941, 'Superman Returns'),
  (-0.3333333333333333, 'Just My Luck'),
  (-0.5663521139548527, 'The Night Listener'),
  (-0.6454972243679047, 'You, Me and Dupree')],
 'Just My Luck': [(0.5555555555555556, 'The Night Listener'),
  (-0.3333333333333333, 'Snakes on a Plane'),
  (-0.42289003161103106, 'Superman Returns'),
  (-0.4856618642571827, 'You, Me and Dupree'),
  (-0.9449111825230676, 'Lady in the Water')],
 'Superman Returns': [(0.6579516949597695, 'You, Me and Dupree'),
  (0.4879500364742689, 'Lady in the Water'),
  (0.11180339887498941, 'Snakes on a Plane'),
  (-0.1798471947990544, 'The Night Listener'),
  (-0.42289003161103106, 'Just My Luck')],
 'You, Me and

In [38]:
#加权平均获得推荐
def getRecommendItems(datadic,computedSim,user):
    userRating=datadic[user]
    scores={}
    totalsim={}
    
#     遍历当前用户评分的物品
    for (item,rating) in userRating.items():
#         遍历与当前物品相近的物品
        for (similarity,item2) in computedSim[item]:
#         如果做过评价，则忽略
            if item2 in userRating:
                continue
#         评价值与相似度加权
            scores.setdefault(item2,0)
            scores[item2]+=similarity*rating
#         全部相似度之和
            totalsim.setdefault(item2,0)
            totalsim[item2]+=similarity
    rankings=[(score/totalsim[item],item) for item,score in scores.items()]
    
#     排序返回结果
    rankings.sort()
    rankings.reverse()
    return rankings

In [39]:
getRecommendItems(critics,itemSim,'Toby')

[(3.610031066802183, 'Lady in the Water'),
 (3.5313950341859766, 'The Night Listener'),
 (2.960999860724268, 'Just My Luck')]

In [3]:
user_table=pd.read_table("F:\\Mycode\\ml-100k\\u.data",header=None,names=["user_id","movie_id","rating","rating_time"])
user_table

user_id  movie_id  rating  rating_time
0          196       242       3    881250949
1          186       302       3    891717742
2           22       377       1    878887116
3          244        51       2    880606923
4          166       346       1    886397596
5          298       474       4    884182806
6          115       265       2    881171488
7          253       465       5    891628467
8          305       451       3    886324817
9            6        86       3    883603013
10          62       257       2    879372434
11         286      1014       5    879781125
12         200       222       5    876042340
13         210        40       3    891035994
14         224        29       3    888104457
15         303       785       3    879485318
16         122       387       5    879270459
17         194       274       2    879539794
18         291      1042       4    874834944
19         234      1184       2    892079237
20         119       392       4    886176814
21         167       486       4    892738452
22         299       144       4    877881320
23         291       118       2    874833878
24         308         1       4    887736532
25          95       546       2    879196566
26          38        95       5    892430094
27         102       768       2    883748450
28          63       277       4    875747401
29         160       234       5    876861185
...        ...       ...     ...          ...
99970      449       120       1    879959573
99971      661       762       2    876037121
99972      721       874       3    877137447
99973      821       151       4    874792889
99974      764       596       3    876243046
99975      537       443       3    886031752
99976      618       628       2    891308019
99977      487       291       3    883445079
99978      113       975       5    875936424
99979      943       391       2    888640291
99980      864       685       4    888891900
99981      750       323       3    879445877
99982      279        64       1    875308510
99983      646       750       3    888528902
99984      654       370       2    887863914
99985      617       582       4    883789294
99986      913       690       3    880824288
99987      660       229       2    891406212
99988      421       498       4    892241344
99989      495      1091       4    888637503
99990      806       421       4    882388897
99991      676       538       4    892685437
99992      721       262       3    877137285
99993      913       209       2    881367150
99994      378        78       3    880056976
99995      880       476       3    880175444
99996      716       204       5    879795543
99997      276      1090       1    874795795
99998       13       225       2    882399156
99999       12       203       3    879959583

[100000 rows x 4 columns]

In [15]:
# 输出存储电影信息的Json对象
movies={}
for line in open("F:\\Mycode\\ml-100k\\u.item",'r',encoding='iso8859-1'):
    (id,title)=line.split('|')[0:2]
    movies[id]=title
movies

{'1': 'Toy Story (1995)',
 '2': 'GoldenEye (1995)',
 '3': 'Four Rooms (1995)',
 '4': 'Get Shorty (1995)',
 '5': 'Copycat (1995)',
 '6': 'Shanghai Triad (Yao a yao yao dao waipo qiao) (1995)',
 '7': 'Twelve Monkeys (1995)',
 '8': 'Babe (1995)',
 '9': 'Dead Man Walking (1995)',
 '10': 'Richard III (1995)',
 '11': 'Seven (Se7en) (1995)',
 '12': 'Usual Suspects, The (1995)',
 '13': 'Mighty Aphrodite (1995)',
 '14': 'Postino, Il (1994)',
 '15': "Mr. Holland's Opus (1995)",
 '16': 'French Twist (Gazon maudit) (1995)',
 '17': 'From Dusk Till Dawn (1996)',
 '18': 'White Balloon, The (1995)',
 '19': "Antonia's Line (1995)",
 '20': 'Angels and Insects (1995)',
 '21': 'Muppet Treasure Island (1996)',
 '22': 'Braveheart (1995)',
 '23': 'Taxi Driver (1976)',
 '24': 'Rumble in the Bronx (1995)',
 '25': 'Birdcage, The (1996)',
 '26': 'Brothers McMullen, The (1995)',
 '27': 'Bad Boys (1995)',
 '28': 'Apollo 13 (1995)',
 '29': 'Batman Forever (1995)',
 '30': 'Belle de jour (1967)',
 '31': 'Crimson Tide

In [18]:
# 输出存储偏好的Json对象
prefers={}
for line in open("F:\\Mycode\\ml-100k\\u.data",'r'):
    (user,movieid,rating,ts)=line.split('\t')
    prefers.setdefault(user,{})
    prefers[user][movies[movieid]]=float(rating)
prefers
# prefers只有943的长度，因为只有943个不重复的user_id,在u.data数据中其实是一条一条用户对电影的评分

{'196': {'Kolya (1996)': 3.0,
  'Mrs. Doubtfire (1993)': 4.0,
  "Muriel's Wedding (1994)": 4.0,
  'Shall We Dance? (1996)': 3.0,
  'Stand by Me (1986)': 5.0,
  'Ace Ventura: Pet Detective (1994)': 5.0,
  'Mrs. Brown (Her Majesty, Mrs. Brown) (1997)': 4.0,
  'Raising Arizona (1987)': 4.0,
  'Being There (1979)': 5.0,
  'Truth About Cats & Dogs, The (1996)': 4.0,
  'Englishman Who Went Up a Hill, But Came Down a Mountain, The (1995)': 2.0,
  'Birdcage, The (1996)': 4.0,
  'English Patient, The (1996)': 5.0,
  'Home Alone (1990)': 3.0,
  'American President, The (1995)': 5.0,
  'Babe (1995)': 5.0,
  'Harold and Maude (1971)': 4.0,
  'Up in Smoke (1978)': 4.0,
  'Four Weddings and a Funeral (1994)': 3.0,
  'While You Were Sleeping (1995)': 3.0,
  'Men in Black (1997)': 2.0,
  'Kids in the Hall: Brain Candy (1996)': 4.0,
  'Groundhog Day (1993)': 3.0,
  'Boogie Nights (1997)': 3.0,
  "Marvin's Room (1996)": 3.0,
  'Cold Comfort Farm (1995)': 3.0,
  'Adventures of Priscilla, Queen of the Des

In [23]:
prefers['12']

{'Air Force One (1997)': 4.0,
 'Jurassic Park (1993)': 4.0,
 'Terminator 2: Judgment Day (1991)': 4.0,
 'Philadelphia (1993)': 5.0,
 'Courage Under Fire (1996)': 5.0,
 'Empire Strikes Back, The (1980)': 4.0,
 'Sound of Music, The (1965)': 5.0,
 'Dances with Wolves (1990)': 5.0,
 'Back to the Future (1985)': 5.0,
 'Wizard of Oz, The (1939)': 5.0,
 'Platoon (1986)': 5.0,
 'Lion King, The (1994)': 4.0,
 "Mr. Holland's Opus (1995)": 5.0,
 'Amadeus (1984)': 5.0,
 'Dead Poets Society (1989)': 5.0,
 'Red Corner (1997)': 4.0,
 'Leaving Las Vegas (1995)': 4.0,
 'Burnt By the Sun (1994)': 5.0,
 'In the Line of Fire (1993)': 5.0,
 'Apollo 13 (1995)': 5.0,
 "Muriel's Wedding (1994)": 4.0,
 'Ghost (1990)': 5.0,
 'Shining, The (1980)': 1.0,
 'Star Wars (1977)': 4.0,
 "Schindler's List (1993)": 5.0,
 'Time to Kill, A (1996)': 5.0,
 'Cinema Paradiso (1988)': 4.0,
 'Man Without a Face, The (1993)': 4.0,
 'Gone with the Wind (1939)': 4.0,
 'Terminator, The (1984)': 4.0,
 'Groundhog Day (1993)': 4.0,
 'K

In [44]:
# 基于用户的推荐
getRecommendations(prefers,'87')[0:30]

[(5.0, 'They Made Me a Criminal (1939)'),
 (5.0, 'Star Kid (1997)'),
 (5.0, 'Santa with Muscles (1996)'),
 (5.0, 'Saint of Fort Washington, The (1993)'),
 (5.0, 'Marlene Dietrich: Shadow and Light (1996) '),
 (5.0, 'Great Day in Harlem, A (1994)'),
 (5.0, 'Entertaining Angels: The Dorothy Day Story (1996)'),
 (5.0, 'Boys, Les (1997)'),
 (4.89884443128923, 'Legal Deceit (1997)'),
 (4.815019082242709, 'Letter From Death Row, A (1998)'),
 (4.800260666069042, 'Mrs. Dalloway (1997)'),
 (4.771240079753505, 'Leading Man, The (1996)'),
 (4.7321082983941425, 'Hearts and Minds (1996)'),
 (4.707354190896574, 'Dangerous Beauty (1998)'),
 (4.696244466490867, 'Pather Panchali (1955)'),
 (4.652397061026758, 'Lamerica (1994)'),
 (4.532337612572981, 'Innocents, The (1961)'),
 (4.527998574747076, 'Casablanca (1942)'),
 (4.512903125553784, 'Four Days in September (1997)'),
 (4.510270149719864, 'Everest (1998)'),
 (4.485151301801341, 'Wallace & Gromit: The Best of Aardman Animation (1996)'),
 (4.463287461

In [48]:
# 基于物品的过滤
itemsim=calculateSimItem(prefers,n=50)
itemsim

{'Kolya (1996)': [(1.000000000000004, 'Basketball Diaries, The (1995)'),
  (1.0000000000000007, 'Waiting to Exhale (1995)'),
  (1.0000000000000007, 'Lightning Jack (1994)'),
  (1.0000000000000007, 'Exit to Eden (1994)'),
  (1.0000000000000004, 'In Love and War (1996)'),
  (1.0000000000000002, 'Gang Related (1997)'),
  (1.0, 'unknown'),
  (1, 'You So Crazy (1994)'),
  (1.0, 'Year of the Horse (1997)'),
  (1, 'Yankee Zulu (1994)'),
  (1, 'Woman in Question, The (1950)'),
  (1, 'Witness (1985)'),
  (1.0, 'Withnail and I (1987)'),
  (1, 'Wings of Courage (1995)'),
  (1.0, 'Wild Bill (1995)'),
  (1, 'Wife, The (1995)'),
  (1, "Wend Kuuni (God's Gift) (1982)"),
  (1, 'Wedding Bell Blues (1996)'),
  (1, 'War at Home, The (1996)'),
  (1, 'Walk in the Sun, A (1945)'),
  (1, 'Vie est belle, La (Life is Rosey) (1987)'),
  (1, 'Very Natural Thing, A (1974)'),
  (1, 'Vermont Is For Lovers (1992)'),
  (1.0, 'Vermin (1998)'),
  (1.0, 'Van, The (1996)'),
  (1.0, 'U.S. Marshalls (1998)'),
  (1.0, 'Two 

In [50]:
getRecommendItems(prefers,itemsim,'87')[0:30]

[(5.0, 'U Turn (1997)'),
 (5.0, 'Robocop 3 (1993)'),
 (5.0, 'Ponette (1996)'),
 (5.0, 'Pather Panchali (1955)'),
 (5.0, 'Of Human Bondage (1934)'),
 (5.0, 'Nénette et Boni (1996)'),
 (5.0, 'Nina Takes a Lover (1994)'),
 (5.0, 'New Jersey Drive (1995)'),
 (5.0, 'Neon Bible, The (1995)'),
 (5.0, 'Nelly & Monsieur Arnaud (1995)'),
 (5.0, 'Murder, My Sweet (1944)'),
 (5.0, 'Midnight Dancers (Sibak) (1994)'),
 (5.0, 'Marlene Dietrich: Shadow and Light (1996) '),
 (5.0, 'Manny & Lo (1996)'),
 (5.0, 'Man of the Year (1995)'),
 (5.0, 'Mad Dog Time (1996)'),
 (5.0, 'Love and Death on Long Island (1997)'),
 (5.0, 'Loch Ness (1995)'),
 (5.0, 'Little City (1998)'),
 (5.0, 'Line King: Al Hirschfeld, The (1996)'),
 (5.0, 'Life Less Ordinary, A (1997)'),
 (5.0, 'Letter From Death Row, A (1998)'),
 (5.0, 'Legal Deceit (1997)'),
 (5.0, 'Lay of the Land, The (1997)'),
 (5.0, 'Late Bloomers (1996)'),
 (5.0, 'Last Summer in the Hamptons (1995)'),
 (5.0, 'Johnny 100 Pesos (1993)'),
 (5.0, 'Jaws 3-D (1983)'